In [1]:
import torch
from torch_geometric.nn import knn_graph, knn


import numpy as np
from tqdm import tqdm

import os
import glob
import re
import json

# sys.path.append('../Utility Scripts')

from Utility_functions import print_3D_graph, manual_print_3D_graph

import params

print('NSIM:', params.NSIM)
print('NSTEP:', params.NSTEP)
print('FLUID_PROBES:', params.NFLUID_PROBES)
print('IO_PROBES:', params.NIO_PROBES)
print('NPOS:', params.NPOS)
print('NFEATURES:', params.NFEATURES)
print('DATADIR:', params.DATADIR)

NSIM: 75
NSTEP: 7000
FLUID_PROBES: 848
IO_PROBES: 0
NPOS: 6
NFEATURES: 10
DATADIR: ../.data/Dataset_75sims


In [2]:

# test_sim000 = np.load("../.data/Extracted_data/probes/SIM000_probepos.npy")

# print(len(test_sim000))
# print(test_sim000) 

In [3]:

# test_sim000 = np.load("../.data/Extracted_data/fields/SIM000_features.npz")

# print(test_sim000.files)

# for name in test_sim000.files:
#     print(f"{name}:")
#     print(test_sim000[name].tolist())
#     print(test_sim000[name].shape)
#     print(len(test_sim000[name]))
#     print("\n" + "-"*50 + "\n")  

# READING NPZ AND NPY

In [4]:
numbers = re.compile(r'(\d+)')

def numericalSort(value):
    parts = numbers.split(value)
    parts[1::2] = map(int, parts[1::2])
    return parts

In [5]:
probes_path = os.path.join(params.DATADIR, 'probes')
probes = sorted(glob.glob(os.path.join(probes_path, '*.npy')), key = numericalSort)
print(probes[0])

fields_path = os.path.join(params.DATADIR, 'fields')
fields = sorted(glob.glob(os.path.join(fields_path, '*.npz')), key = numericalSort)
print(fields[0])

../.data/Dataset_75sims\probes\SIM000_probepos.npy
../.data/Dataset_75sims\fields\SIM000_features.npz


In [6]:
# probe_data_list = []

# for data_file in probes:
#     read_points = np.load(data_file)
#     probe_data_list.append(torch.from_numpy(read_points))

# pos_list = probe_data_list
# #print(pos_list)
# print(len(pos_list))
# print(pos_list[0].tolist())
# print(len(pos_list[0]))
# print(pos_list[0])


In [7]:
features_list = []

for data_file in fields:
    read_features = np.load(data_file)
    num_points = None
    for _, filedat in enumerate(read_features.files):
        if num_points is None:
            num_points = len(read_features[filedat])
            # print(len(read_features[filedat]))
            feature_tensor = torch.zeros(num_points, 10)
            # print(len(feature_tensor))
        #print(read_features[filedat])
        feature_tensor[:, _] = torch.from_numpy(read_features[filedat]).squeeze()
    features_list.append(feature_tensor)

feat_list = features_list
print(feat_list[0])
print(len(feat_list))

tensor([[ 1.0634e+05, -7.0602e-03, -4.6890e-02,  ...,  3.5704e+02,
          2.5600e+00,  0.0000e+00],
        [ 1.1045e+05,  7.1255e+00, -3.4014e+00,  ...,  3.5704e+02,
          2.5600e+00,  0.0000e+00],
        [ 1.1028e+05,  4.8828e+00, -4.0602e+00,  ...,  3.5704e+02,
          2.5600e+00,  0.0000e+00],
        ...,
        [ 1.0555e+05, -1.4050e-01,  1.1419e-01,  ...,  3.5704e+02,
          2.5600e+00,  0.0000e+00],
        [ 1.1317e+05,  4.4859e+00, -1.1467e+01,  ...,  3.5704e+02,
          2.5600e+00,  0.0000e+00],
        [ 1.0059e+05,  5.9168e+00,  7.3010e-01,  ...,  3.5704e+02,
          2.5600e+00,  0.0000e+00]])
75


In [8]:
print(len(probes))
assert params.NSIM == len(probes)

dataset_len = len(probes)  # number of simulations
print(probes)
positions = np.empty((params.NSIM, params.NPOS, params.NFLUID_PROBES + params.NIO_PROBES))
#print(positions)
for i, data in enumerate(probes):
    read_points = np.load(data)
    #print(read_points)
    positions[i,:] = read_points.T
    
pos = torch.from_numpy(np.einsum('ijk->ikj', positions))
print(len(pos))
print(pos[0])
#print(pos[1])
print(pos.shape) # [params.NSIM, params.NFLUID_PROBES + params.NIO_PROBES, params.NPOS]

75
['../.data/Dataset_75sims\\probes\\SIM000_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM001_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM002_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM003_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM004_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM005_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM006_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM007_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM008_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM009_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM010_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM011_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM012_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM013_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM014_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM015_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM016_probepos.npy', '../.data/Dataset_75sims\\probes\\SIM017_pro

In [9]:
# features = np.empty((params.NSIM, params.NSIM * NUM_FEATURES, NUM_NODES))
####positions = np.empty((params.NSIM, params.NPOS, params.NFLUID_PROBES + params.NIO_PROBES))
features = np.zeros((params.NSIM, params.NFRAME * params.NFEATURES, params.NFLUID_PROBES + params.NIO_PROBES))
feat = features.reshape((params.NSIM, params.NFRAME, params.NFEATURES, params.NFLUID_PROBES + params.NIO_PROBES))
# print(features.shape)
# #print(feat)
# print('Features shape:', features.shape)     # [1000, 60 (6*10), 2000]
#print(fields)
for i, data in enumerate(tqdm(fields)):

    read_features = np.load(data)
    print(read_features.files)
    print(read_features)
    for j, filedat in enumerate(read_features.files): 
        # print(i, j, filedat, read_features[filedat].shape, features[i, j, :].shape)
        #features[i, j, :params.NFLUID_PROBES] = read_features[filedat]
        # print(read_features[filedat])
        features[i, j, :] = read_features[filedat]
        #print(features[i, j, :params.NFLUID_PROBES])

#print(features[0][0].tolist())

100%|██████████| 75/75 [00:00<00:00, 904.63it/s]

['p', 'U_x', 'U_y', 'U_z', 'T', 'rho', 'phi', 'real_velocity_0', 'real_angle_0', 'zero3']
NpzFile '../.data/Dataset_75sims\\fields\\SIM000_features.npz' with keys: p, U_x, U_y, U_z, T...
['p', 'U_x', 'U_y', 'U_z', 'T', 'rho', 'phi', 'real_velocity_0', 'real_angle_0', 'zero3']
NpzFile '../.data/Dataset_75sims\\fields\\SIM001_features.npz' with keys: p, U_x, U_y, U_z, T...
['p', 'U_x', 'U_y', 'U_z', 'T', 'rho', 'phi', 'real_velocity_0', 'real_angle_0', 'zero3']
NpzFile '../.data/Dataset_75sims\\fields\\SIM002_features.npz' with keys: p, U_x, U_y, U_z, T...
['p', 'U_x', 'U_y', 'U_z', 'T', 'rho', 'phi', 'real_velocity_0', 'real_angle_0', 'zero3']
NpzFile '../.data/Dataset_75sims\\fields\\SIM003_features.npz' with keys: p, U_x, U_y, U_z, T...
['p', 'U_x', 'U_y', 'U_z', 'T', 'rho', 'phi', 'real_velocity_0', 'real_angle_0', 'zero3']
NpzFile '../.data/Dataset_75sims\\fields\\SIM004_features.npz' with keys: p, U_x, U_y, U_z, T...
['p', 'U_x', 'U_y', 'U_z', 'T', 'rho', 'phi', 'real_velocity_0', 

In [10]:
#print(features[0][1].tolist()) # vel_x
feat = features.reshape((params.NSIM, params.NFRAME, params.NFEATURES, params.NFLUID_PROBES + params.NIO_PROBES))

feat = torch.from_numpy(np.einsum('ijkl->ijlk', feat))
print(feat.shape)
print(feat[0][0].tolist()) 
#print(len(feat[0][0]))

torch.Size([75, 1, 848, 10])
[[106343.0, -0.00706015, -0.0468903, 338.435, 300.854, 1.22862, -7.48013, 357.04, 2.56, 0.0], [110449.0, 7.12555, -3.40143, 326.432, 304.944, 1.25893, 0.894384, 357.04, 2.56, 0.0], [110285.0, 4.88276, -4.06016, 326.192, 305.455, 1.25496, 6664.04, 357.04, 2.56, 0.0], [105994.0, -0.0455933, -0.0835729, 339.29, 300.464, 1.22617, -8.7628, 357.04, 2.56, 0.0], [107311.0, 0.0316137, -0.0218799, 336.884, 301.921, 1.23542, 26.7877, 357.04, 2.56, 0.0], [100855.0, 5.00259, -14.3533, 348.888, 295.791, 1.18515, 2.05925, 357.04, 2.56, 0.0], [102320.0, 7.43432, -11.6077, 345.182, 297.16, 1.19684, -1.14003, 357.04, 2.56, 0.0], [107313.0, 0.0193253, -0.0996728, 336.583, 301.571, 1.23687, -14.2031, 357.04, 2.56, 0.0], [107310.0, 0.0945333, 0.0446411, 336.852, 301.953, 1.23528, -1.56629, 357.04, 2.56, 0.0], [108173.0, -1.30883, -2.19812, 333.552, 302.14, 1.24444, -2.21252, 357.04, 2.56, 0.0], [108815.0, -0.609553, -1.22632, 332.322, 302.69, 1.24955, -0.50642, 357.04, 2.56, 0.

In [11]:
# new_pos_list = [pos.unsqueeze(0).repeat(params.NFRAME, 1, 1) for pos in pos_list]
# print('Node position and labels data:', [pos.shape for pos in new_pos_list])
# print('Fluid dynamic features   data:', [feat.shape for feat in feat_list])

# dataset = [torch.cat([new_pos, feat.unsqueeze(0)], dim=-1) for new_pos, feat in zip(new_pos_list, feat_list)]

# print('Concatenated total data:', [data.shape for data in dataset])


In [12]:
new_pos = pos.unsqueeze(1).repeat(1, params.NFRAME, 1, 1)
print('Node position and labels data:', new_pos.shape)
print('Fluid dynamic features   data:', feat.shape)

dataset = torch.cat([new_pos, feat], dim = -1)
print(len(dataset))
print(dataset[0][0][0])

print('Concatenated total data:', dataset.shape) # [100,6,2100,16]

Node position and labels data: torch.Size([75, 1, 848, 6])
Fluid dynamic features   data: torch.Size([75, 1, 848, 10])
75
tensor([-7.3824e-01, -1.6011e+00, -1.4983e+01,  0.0000e+00,  0.0000e+00,
         0.0000e+00,  1.0634e+05, -7.0602e-03, -4.6890e-02,  3.3844e+02,
         3.0085e+02,  1.2286e+00, -7.4801e+00,  3.5704e+02,  2.5600e+00,
         0.0000e+00], dtype=torch.float64)
Concatenated total data: torch.Size([75, 1, 848, 16])


In [13]:
# cut to last frame, we are interested in the steady state

print('Data with all time frames:', dataset.shape)     # [1000,6,2100,16] [samples,frames, nodes, tot_features]

new_dataset = dataset[:, -1:, :, :].squeeze(1) # only last frame
print(new_dataset[0][0]) # coord_x, coord_y, coord_z, mis, size, sdf, press, vel_x, vel_y, vel_z, stress_ij

print('Data with only last frame:', new_dataset.shape)    # [samples, 2100, 16]

Data with all time frames: torch.Size([75, 1, 848, 16])
tensor([-7.3824e-01, -1.6011e+00, -1.4983e+01,  0.0000e+00,  0.0000e+00,
         0.0000e+00,  1.0634e+05, -7.0602e-03, -4.6890e-02,  3.3844e+02,
         3.0085e+02,  1.2286e+00, -7.4801e+00,  3.5704e+02,  2.5600e+00,
         0.0000e+00], dtype=torch.float64)
Data with only last frame: torch.Size([75, 848, 16])


# PREPROCESSING OF MIS VALUES

In [14]:
# clean up MIS to have smooth values next to wall (due to the staircase-like discretization)

spacing = params.SPACING
kneigh_shells = params.NEIGHBOURS

idx = 0
nodes = new_dataset.shape[1]
# edge_index = knn_graph(new_dataset[idx,:,:3], params.NEIGHBOURS)
edge_index = torch.tensor(np.load(params.DATADIR+"/connectivity.npy"))
print(edge_index)
# print('knn_graph:', edge_index.shape)
print(edge_index.shape)
print(edge_index)

for idx in range(0):
    print_3D_graph(new_dataset[idx,:,:3], edge_index, color = new_dataset[idx,:,4]) # original

# for data in tqdm(new_dataset):

#     print(data)
#     # selecting near-surface nodes (outer shell)
#     idx_shell1 = (data[:,3] <= spacing)
#     pos_shell1 = data[idx_shell1,:3]

#     # selecting near-to-outer shell nodes
#     idx_shell2 = (data[:,3]>spacing)*(data[:,3]<=3*spacing)
#     pos_shell2 = data[idx_shell2,:3]

#     # ordered array of the two shells' nodes
#     shells_pos = torch.cat((pos_shell1,pos_shell2),0)

#     # creating edges between set1 and set2
#     edge_indexes = knn(pos_shell2,pos_shell1, kneigh_shells)

#     # storing indexes of edge-receiving nodes
#     edge_reshaped = edge_indexes.reshape(-1)[int(sum(idx_shell1)*kneigh_shells):]

#     # get the MIS value for the edge-receiving nodes
#     sdf_reshaped = data[idx_shell2][edge_reshaped][:,4].reshape(-1,kneigh_shells)

#     def most_frequent(row):
#         i = 0
#         values, counts = np.unique(row, return_counts=True)
#         ind = np.argmax(counts)
#         return values[ind]

#     # for every row, calculate the most occurring MIS value
#     # the i-th row represents the i-th edge-sending node (nodes belonging to the outer shell)
#     new_val = np.apply_along_axis(most_frequent, 1, sdf_reshaped)

#     # change outer shell's MIS values with the ones computed now
#     data[idx_shell1,4] = torch.tensor(new_val)

#     # indexing on the whole set of points has to be coherent with nodes ordering 
#     # (knn function with two sets of nodes, orders both indexing from 0)
#     edge_indexes_plot = edge_indexes.clone()
#     edge_indexes_plot[1,:] += edge_indexes_plot[0,-1]+1


# print_3D_graph(new_dataset[idx,:,:3], edge_index, color = new_dataset[idx,:,4]) # processed

tensor([[  0,   0,   0,  ..., 847, 847, 847],
        [401,   1, 307,  ..., 800, 719, 194]])
torch.Size([2, 8480])
tensor([[  0,   0,   0,  ..., 847, 847, 847],
        [401,   1, 307,  ..., 800, 719, 194]])


# READ A GRAPH AND CONSTRUCT EDGE CONNECTIVITY

In [15]:
# check if given the big tensor storing all simulations, I am able to recover a specific steady state and its quantities

for i in range(1):
    single_graph = new_dataset[i,...]

    # i=0
    # while i < 61:#len(single_graph):
    #     print(f"{i}th node: {torch.norm(single_graph[i,7:10])}")
    #     i += 1

    neighbours = params.NEIGHBOURS

    # print(single_graph[1]) # coord_x, coord_y, coord_z, mis, sdf, size, press, vel_x, vel_y, vel_z, stress_ij

    for i in range(3):
        print(single_graph[i, 7:10].tolist())

    #magvel = torch.norm(single_graph[..., 4:7], dim=-1)
    magvel = torch.norm(single_graph[..., 7:10], dim=-1) # 7:10 are vel_x, vel_y, vel_z
    print(f"magvel: {magvel}")   

    print('Single graph:', single_graph.shape)
    # print('Edge index  :', edge_index.shape)
    print('Velocity magnitude:', magvel.shape)

    print(" ")
    print("VELOCITY:")
    print_3D_graph(single_graph, edge_index, magvel)

    # [(0, -1), (0, 1), (1, 2), (1, 4), (2, 3),
    # (4, 5), (3, 6), (3, 8), (5, 10), (5, 12), 
    # (6, 7), (8, 9), (10, 11), (12, 13)]

[-0.00706015, -0.0468903, 338.435]
[7.12555, -3.40143, 326.432]
[4.88276, -4.06016, 326.192]
magvel: tensor([338.4350, 326.5275, 326.2538, 339.2900, 336.8840, 349.2190, 345.4571,
        336.5830, 336.8520, 333.5618, 332.3248, 336.5580, 334.6751, 328.8402,
        333.2466, 335.3630, 317.1532, 351.5009, 349.6895, 287.6609, 328.3248,
        340.0063, 338.7610, 332.0048, 341.0291, 337.8350, 332.8655, 337.7560,
        335.1200, 333.9080, 354.2161, 356.4924, 343.1922, 353.7972, 331.9100,
        330.3993, 339.3002, 393.4740, 385.4855, 339.1052, 344.1222, 351.2972,
        337.6502, 354.6155, 338.8651, 329.8365, 333.5194, 338.8951, 338.4930,
        331.6230, 332.4482, 339.5190, 203.1864, 200.6201, 175.7259, 356.6404,
        359.4445, 171.8299, 325.2141, 356.2881, 359.8582, 331.8707, 360.4512,
        317.4439, 328.9195, 372.8164, 333.1769, 337.8070, 330.1478, 328.3327,
        337.8620, 328.6734, 386.7132, 329.5608, 385.8491, 331.8949, 332.7235,
        337.8520, 328.0387, 320.7813, 337

# READ PRESSURE

In [16]:

single_graph = new_dataset[0,...]

press = single_graph[..., 6] # 6th column is pressure
print(press.tolist())
print(" ")
print("PRESSURE:")
print_3D_graph(single_graph, edge_index, press)


[106343.0, 110449.0, 110285.0, 105994.0, 107311.0, 100855.0, 102320.0, 107313.0, 107310.0, 108173.0, 108815.0, 107311.0, 108245.0, 107445.0, 107624.0, 107838.0, 107277.0, 100831.0, 101713.0, 107535.0, 110657.0, 106022.0, 106376.0, 109178.0, 105479.0, 106726.0, 108932.0, 106728.0, 107817.0, 108219.0, 100105.0, 98979.2, 104526.0, 100274.0, 109182.0, 107659.0, 106012.0, 83060.2, 86330.5, 106076.0, 104098.0, 101084.0, 106327.0, 99540.9, 106299.0, 109884.0, 108432.0, 106330.0, 106346.0, 109322.0, 108967.0, 106016.0, 105688.0, 105483.0, 101335.0, 99002.6, 97818.7, 101199.0, 110225.0, 98725.5, 97348.2, 108369.0, 97258.8, 108696.0, 107785.0, 90782.4, 108757.0, 106734.0, 109831.0, 110651.0, 106762.0, 109185.0, 85756.5, 108504.0, 86000.0, 108302.0, 108930.0, 106737.0, 110651.0, 113559.0, 106737.0, 104675.0, 108102.0, 107466.0, 102030.0, 102850.0, 107441.0, 106241.0, 103855.0, 107000.0, 107731.0, 107631.0, 107574.0, 107540.0, 106236.0, 107815.0, 108238.0, 108129.0, 107825.0, 107942.0, 107869.0, 1

# CHECKING MIS PREPROCESSING

In [17]:
# idx = 0 # steady state idx
# neighbours = params.NEIGHBOURS
# nodes = new_dataset.shape[1]
# new_dataset_copy = new_dataset.clone()

# # print(new_dataset_copy.shape)

# print_3D_graph(new_dataset_copy[idx,:,:3], edge_index, color = new_dataset_copy[idx,:,4]) # original    
# print_3D_graph(new_dataset[idx,:,:3], edge_index, color = new_dataset[idx,:,4]) # processed

In [18]:
# counts = []

# # checking number of neighbors per node
# for i in range(params.NFLUID_PROBES + params.NIO_PROBES):
#     count = (edge_index[1,:] == i)
#     count = count.sum()
#     counts.append(count)

# print('edge_index[:10]', edge_index[:10])
# print('counts[:10]:', counts[:10])

# count = torch.tensor(counts, dtype=torch.float32)
# print('Mean:', count.mean(), 'Std:', count.std())

# NORMALIZE DATASET

In [19]:
print(f"pre normalization: {new_dataset[0][0]}")
print(f"pre normalization: {new_dataset[0][0][6:-1]}")
new_dataset.shape

print(new_dataset[:, :, 6].min())

pre normalization: tensor([-7.3824e-01, -1.6011e+00, -1.4983e+01,  0.0000e+00,  0.0000e+00,
         0.0000e+00,  1.0634e+05, -7.0602e-03, -4.6890e-02,  3.3844e+02,
         3.0085e+02,  1.2286e+00, -7.4801e+00,  3.5704e+02,  2.5600e+00,
         0.0000e+00], dtype=torch.float64)
pre normalization: tensor([ 1.0634e+05, -7.0602e-03, -4.6890e-02,  3.3844e+02,  3.0085e+02,
         1.2286e+00, -7.4801e+00,  3.5704e+02,  2.5600e+00],
       dtype=torch.float64)
tensor(47538.1000, dtype=torch.float64)


In [20]:

cols_params = {
    'pressure_min': None,
    'pressure_max': None,
    'vel_x_min': None,
    'vel_x_max': None,
    'vel_y_min': None,
    'vel_y_max': None,
    'vel_z_min': None,
    'vel_z_max': None,
    'temperature_min': None,
    'temperature_max': None,
    'rho_min': None,
    'rho_max': None,
    'phi_min': None,
    'phi_max': None,
    'initial_velocity_min': None,
    'initial_velocity_max': None,
    'initial_aot_min': None,
    'initial_aot_max': None,
}

cols_to_normalize = new_dataset[:, :, 6:-1]

keys = list(cols_params.keys())
for i in range(cols_to_normalize.shape[2]):

    col = cols_to_normalize[:, :, i]
    col_min = col.min()
    col_max = col.max()

    cols_to_normalize[:, :, i] = (col - col_min) / (col_max - col_min)

    cols_params[keys[i * 2]] = col_min.item()
    cols_params[keys[i * 2 + 1]] = col_max.item()

# save parametrizations params
with open(params.DATADIR+'/normalization_params.json', 'w') as f:
    json.dump(cols_params, f)


new_dataset[:, :, 6:-1] = cols_to_normalize

new_dataset[:, :, 5] = 2 # size -> 2 for fluid nodes

print(cols_params)


{'pressure_min': 47538.1, 'pressure_max': 126238.0, 'vel_x_min': -33.7811, 'vel_x_max': 86.3179, 'vel_y_min': -67.0429, 'vel_y_max': 22.2151, 'vel_z_min': 151.442, 'vel_z_max': 418.419, 'temperature_min': 240.672, 'temperature_max': 342.852, 'rho_min': 0.686562, 'rho_max': 1.38032, 'phi_min': -1668.63, 'phi_max': 6681.82, 'initial_velocity_min': 321.01, 'initial_velocity_max': 359.98, 'initial_aot_min': -9.23, 'initial_aot_max': 9.8}


In [21]:
print(f"post normalization: {new_dataset[0][0]}")
new_dataset.shape

print(new_dataset[:, :, 6].min())

post normalization: tensor([ -0.7382,  -1.6011, -14.9834,   0.0000,   0.0000,   2.0000,   0.7472,
          0.2812,   0.7506,   0.7004,   0.5890,   0.7813,   0.1989,   0.9246,
          0.6195,   0.0000], dtype=torch.float64)
tensor(0., dtype=torch.float64)


# SAVING DATASET

In [22]:
saved_dataset = new_dataset.reshape(-1, params.NFLUID_PROBES + params.NIO_PROBES, params.NFEATURES + 6).float()


In [23]:
raw_path = os.path.join(params.DATADIR, 'raw')
processed_path = os.path.join(params.DATADIR, 'processed')
dataset_name = 'Dataset.pt'

if not os.path.exists(raw_path):
    os.makedirs(raw_path)

if not os.path.exists(processed_path):
    os.makedirs(processed_path)

torch.save(saved_dataset, os.path.join(raw_path, dataset_name))